# Setup
---

In [1]:
%load_ext rpy2.ipython

import os

import numpy as np
import pandas as pd
import pystan
import statsmodels.api as sm
from bokeh.io import output_notebook
from bokeh.layouts import gridplot
from bokeh.models import ColumnDataSource, HoverTool, Span
from bokeh.plotting import figure, show
from IPython.display import display, HTML

NOTEBOOKS_DIR = os.path.abspath(os.curdir)
LIB_DIR = os.path.abspath(os.path.join(NOTEBOOKS_DIR, '..'))
DATA_DIR = os.path.join(LIB_DIR, 'data')
DATA_FILENAME = 'count-data.csv'
DATA_FILEPATH = os.path.join(DATA_DIR, DATA_FILENAME)

output_notebook()

/usr/local/miniconda3/envs/StanCon2018_Intro/lib/python3.6/site-packages/statsmodels/compat/pandas.py:56: FutureWarning: The pandas.core.datetools module is deprecated and will be removed in a future version. Please use the pandas.tseries module instead.
  from pandas.core import datetools


Loading BokehJS ...

# Load and examine data
---
R prints data in more concise manner, which is why we will just examine the `head` of the pandas dataframe here.

In [2]:
model_df = pd.read_csv(DATA_FILEPATH, header=None)
model_df.reset_index(inplace=True)
model_df.rename(columns={0: 'data', 'index': 'x'}, inplace=True)
print('Data length: {}'.format(model_df.shape[0]))
display(HTML(model_df.to_html()))

Data length: 500


In [3]:
# Prepare the data for the plot.
model_counts, model_bins = np.histogram(
    model_df['data'],
    bins='auto'
)
model_bin_width = model_bins[1] - model_bins[0]
model_histogram_data = {
    'counts': model_counts,
    'bins': model_bins[1:]
}
model_histogram_df = pd.DataFrame.from_records(model_histogram_data)
model_source = ColumnDataSource(model_histogram_data)

# Create a set of tools for the plot.
tools = 'pan,box_zoom,wheel_zoom,save,reset,help'
hover = HoverTool(
    tooltips=[
        ('Counts', '@counts'),
        ('x', '@bins')
    ]
)
tools = tools.split(',') + [hover]

# Style the plot.
plot_width = 600
plot_height = 600
x_axis_label = 'Data'
y_axis_label = 'Counts'
model_title = 'Stan Con 2018 Introduction - model "unknown" distribution data'

# Create the plot.
model_plot = figure(
    plot_width=plot_width,
    plot_height=plot_height,
    x_axis_label=x_axis_label,
    y_axis_label=y_axis_label,
    title=model_title,
    tools=tools
)

# Bind data to the plot.
model_plot.vbar(
    x='bins',
    width=model_bin_width,
    bottom=0,
    top='counts',
    source=model_source,
    line_color='Black',
    fill_color='Grey',
    legend='Model data',
    alpha=0.5
)

# Show the plot.
show(model_plot)

## Compare our data to draws from a Poisson distribution with the same mean

In [4]:
# Prepare the data for the plot.
poisson_df = pd.DataFrame(data=np.random.poisson(lam=model_df['data'].mean(), size=500))
poisson_df.reset_index(inplace=True)
poisson_df.rename(columns={0: 'data', 'index': 'x'}, inplace=True)
poisson_counts, poisson_bins = np.histogram(
    poisson_df['data'],
    bins='auto'
)
poisson_bin_width = poisson_bins[1] - poisson_bins[0]
poisson_histogram_data = {
    'counts': poisson_counts,
    'bins': poisson_bins[1:]
}
poisson_histogram_df = pd.DataFrame.from_records(poisson_histogram_data)
poisson_source = ColumnDataSource(poisson_histogram_data)

# Style the plot. Most all parameters will be reused here from the above plot.
poisson_title = 'Stan Con 2018 Introduction - Poisson distribution data'

# Create the plot.
poisson_plot = figure(
    plot_width=plot_width,
    plot_height=plot_height,
    x_axis_label=x_axis_label,
    y_axis_label=y_axis_label,
    title=poisson_title,
    tools=tools
)

# Bind data to the plot.
poisson_plot.vbar(
    x='bins',
    width=poisson_bin_width,
    bottom=0,
    top='counts',
    source=poisson_source,
    line_color='Black',
    fill_color='Purple',
    legend='Poisson data',
    alpha=0.5
)

# Show the plot.
show(poisson_plot)

## Frequency Polygons
Python does not have a convience function for creating frequency plots, so we will manipulate the data so we can draw one.

**`NOTE`** This plot was removed from the original `Rmd` file. It is redrawn here as it is an interesting visual.

In [5]:
# Prepare the data for the plot.
min_x = int(min(model_histogram_df['bins'].min(), poisson_histogram_df['bins'].min()))
max_x = int(max(model_histogram_df['bins'].max(), poisson_histogram_df['bins'].max()))

bin_size = 0.5
frequency_polygons_x = []
frequency_polygons_y = []
poisson_frequency_polygons_x = []
poisson_frequency_polygons_y = []
for index in range(min_x, max_x + 1):
    x = [index - 0.5, index, index + 0.5]
    y = [0, model_df[model_df['data'].between(x[0], x[2])].shape[0], 0]
    poisson_y = [0, poisson_df[poisson_df['data'].between(x[0], x[2])].shape[0], 0]
    frequency_polygons_x.extend(x)
    frequency_polygons_y.extend(y)
    poisson_frequency_polygons_x.extend(x)
    poisson_frequency_polygons_y.extend(poisson_y)
frequency_polygons_df = pd.DataFrame(
    data=np.vstack([frequency_polygons_x, frequency_polygons_y]),
).T.rename(columns={0: 'x', 1: 'counts'})
poisson_frequency_polygons_df = pd.DataFrame(
    data=np.vstack([poisson_frequency_polygons_x, poisson_frequency_polygons_y]),
).T.rename(columns={0: 'x', 1: 'counts'})
frequency_polygons_source = ColumnDataSource(
    {
        'y': [frequency_polygons_df['counts'], poisson_frequency_polygons_df['counts']],
        'x': [frequency_polygons_df['x'], poisson_frequency_polygons_df['x']],
        'legend': ['model data', 'Poisson data'],
        'color': ['Grey', 'Purple']
    }
)

# Style the plot. Most all parameters will be reused here from the above plot.
frequency_plot_title = 'Stan Con 2018 Introduction - Frequency Polygons'

# Create a set of tools for the plot.
tools = 'pan,box_zoom,wheel_zoom,save,reset,help'
hover = HoverTool(
    tooltips=[
        ('Counts', '@counts'),
        ('x', '@bins')
    ],
    mode='mouse'
)
tools = tools.split(',') + [hover]


# Create the plot.
frequency_polygons_plot = figure(
    plot_width=plot_width,
    plot_height=plot_height,
    x_axis_label=x_axis_label,
    y_axis_label=y_axis_label,
    title=frequency_plot_title,
    tools=tools
)

# Bind data to the plot.
c = frequency_polygons_plot.multi_line(
    xs='x',
    ys='y',
    legend='legend',
    line_width=2,
    line_color='color',
    source=frequency_polygons_source,
)
a = ColumnDataSource(
    {
        'counts': frequency_polygons_df['counts'],
        'bins': frequency_polygons_df['x'],
    }
)
a_plot = frequency_polygons_plot.circle(
    x='bins',
    y='counts',
    source=a,
    fill_color='Grey',
    line_color='Black',
    size=5,
)
b = ColumnDataSource(
    {
        'counts': poisson_frequency_polygons_df['counts'],
        'bins': poisson_frequency_polygons_df['x'],
    }
)
b_plot = frequency_polygons_plot.circle(
    x='bins',
    y='counts',
    source=b,
    fill_color='Purple',
    line_color='Black',
    size=5,
)
hover.renderers.append(a_plot)
hover.renderers.append(b_plot)


# Show the plot.
show(frequency_polygons_plot)

## Side-by-side bar charts

In [6]:
# Prepare the data for the plot.
model_histogram_source = ColumnDataSource(model_histogram_df)
poisson_histogram_source = ColumnDataSource(poisson_histogram_df)

# Style the plot. Most all parameters will be reused here from the above plot.
comparison_title = 'Stan Con 2018 Introduction - Poisson & model distribution data'

# Create a set of tools for the plot.
tools = 'pan,box_zoom,wheel_zoom,save,reset,help'
hover = HoverTool(
    tooltips=[
        ('Counts', '@counts'),
        ('x', '@bins')
    ]
)
tools = tools.split(',') + [hover]

# Create the plot.
comparison_plot = figure(
    plot_width=plot_width,
    plot_height=plot_height,
    x_axis_label=x_axis_label,
    y_axis_label=y_axis_label,
    title=comparison_title,
    tools=tools
)

# Bind data to the plot.
comparison_plot.vbar(
    x='bins',
    width=model_bin_width,
    bottom=0,
    top='counts',
    source=model_histogram_source,
    fill_color='Grey',
    line_color='Black',
    legend='Model data',
    alpha=0.5
)
comparison_plot.vbar(
    x='bins',
    width=poisson_bin_width,
    bottom=0,
    top='counts',
    source=poisson_histogram_source,
    fill_color='Purple',
    line_color='Black',
    legend='Poisson data',
    alpha=0.5
)

# Show the plot.
show(comparison_plot)

# Fit basic Poisson model
---
Even though we already suspect it won't be a good model for this data, it's still a good idea to start by fitting the simplest Poisson model. From there we can then identify in which ways the model is inadequate.

In [7]:
with open('../stan/poisson-simple.stan', 'r') as open_file:
    for line in open_file:
        print(line.replace('\n', ''))

/* Stan program 
 * for simple Poisson model
 */
data {
  int<lower=1> N;      // Number of observations
  int<lower=0> y[N];   // Count data (integer array)
}
parameters {
  real<lower=0> lambda;  // Poisson rate/mean parameter (must be positive)
}
model {
  lambda ~ exponential(0.2);
  y ~ poisson(lambda);
}
generated quantities {
  int y_rep[N];    // Draws from posterior preditive dist
  real log_lik[N]; // Pointwise log-likelihood contributions
  
  for (n in 1:N) {
    // Draw from posterior predictive distribution
    y_rep[n] = poisson_rng(lambda);
    
    // Compute and store the log-likelihood contribution of each observation
    // (this will be used for the last section of the R markdown document
    // which deals with predictive performance)
    log_lik[n] = poisson_lpmf(y[n] | lambda);
  }
}


In [8]:
basic_fit_data = {
    'N': model_df.shape[0],
    'y': model_df['data']
}
basic_fit = pystan.stan(
    file='../stan/poisson-simple.stan',
    data=basic_fit_data,
    iter=2000,
    warmup=1000,
    chains=4
)
print(basic_fit)

INFO:pystan:COMPILING THE C++ CODE FOR MODEL anon_model_6f2108b6dc0e784a4f4bdb99c8f90344 NOW.


Inference for Stan model: anon_model_6f2108b6dc0e784a4f4bdb99c8f90344.
4 chains, each with iter=2000; warmup=1000; thin=1; 
post-warmup draws per chain=1000, total post-warmup draws=4000.

               mean se_mean     sd   2.5%    25%    50%    75%  97.5%  n_eff   Rhat
lambda         3.66  2.3e-3   0.09   3.49    3.6   3.66   3.72   3.83   1440    1.0
y_rep[0]       3.65    0.03   1.88    1.0    2.0    3.0    5.0    8.0   4000    1.0
y_rep[1]       3.63    0.03   1.91    0.0    2.0    4.0    5.0    8.0   3904    1.0
y_rep[2]       3.73    0.03   1.94    0.0    2.0    4.0    5.0    8.0   3712    1.0
y_rep[3]       3.62    0.03   1.92    1.0    2.0    3.0    5.0    8.0   3988    1.0
y_rep[4]        3.6    0.03   1.91    0.0    2.0    3.0    5.0    8.0   4000    1.0
y_rep[5]       3.66    0.03   1.91    0.0    2.0    3.0    5.0    8.0   3795    1.0
y_rep[6]       3.68    0.03   1.92    1.0    2.0    4.0    5.0    8.0   3902    1.0
y_rep[7]       3.66    0.03    1.9    0.0    2.0    4.0

## Look at posterior distribution of lambda
**`NOTE`** that we need to estimate the density of lambda using the statsmodels package.

In [9]:
# Prepare the data for the plot. We will estimate the density of lambda to mimic
# what is available in R.
y = basic_fit.extract().get('lambda')
kde = sm.nonparametric.KDEUnivariate(y)
kde.fit(bw=0.012)
lambda_data = {
    'support': kde.support,
    'density': kde.density/kde.density.max()
}
lambda_source = ColumnDataSource(lambda_data)
eighty_percent = pd.DataFrame(
    kde.density/kde.density.max()
)[0].between(0.2, 0.8).replace(False, np.nan).dropna().index[[0, -1]].tolist()
band_x = np.append(
    kde.support[eighty_percent[0]:eighty_percent[1]],
    kde.support[eighty_percent[0]:eighty_percent[1]][::-1]
)
band_y = np.append(
    np.zeros(np.diff(eighty_percent)),
    kde.density[eighty_percent[0]:eighty_percent[-1]][::-1]/kde.density.max()
)

# Create tools specific to this plot.
tools = 'pan,box_zoom,wheel_zoom,save,reset,help'
lambda_hover = HoverTool(
    tooltips=[
        ('y', '@density'),
        ('x', '@support')
    ]
)
tools = tools.split(',') + [lambda_hover]

# Style the plot.
x_axis_label = 'lambda'
y_axis_label = 'Arbitrary units'
lambda_title = 'Stan Con 2018 Introduction - Stan fit lambda'

# Create the plot.
lambda_plot = figure(
    plot_width=plot_width,
    plot_height=plot_height,
    x_axis_label=x_axis_label,
    y_axis_label=y_axis_label,
    title=lambda_title,
    tools=tools
)

# Bind data to the plot.
lambda_plot.line(
    x='support',
    y='density',
    source=lambda_source,
    color='Black',
    line_width=2
)
vline = Span(location=y.mean(), dimension='height', line_color='Blue', line_width=2)
lambda_plot.renderers.extend([vline])
lambda_plot.patch(band_x, band_y, color='dodgerblue', alpha=0.5)

# Show the plot.
show(lambda_plot)

## Compare posterior of lambda to the mean of the data
The model gets the mean right, but, as we'll see next, the model is quite bad at predicting the outcome.

In [10]:
print(
    'Posterior mean: {posterior}\n'
    '     Data mean: {data}'.format(
        posterior=round(y.mean(), 2),
        data=round(model_df['data'].mean(), 2)
    )
)

Posterior mean: 3.66
     Data mean: 3.66


## Graphical posterior predictive checks
Extract `y_ref` draws from the fitted model object.

**`NOTE`** that Python does not have an analogous `bayesplot` tool like R has. So, we will just hardcode the plot to mimic what is in the R notebook for continuity.

In [11]:
y_rep_df_basic = pd.DataFrame(basic_fit.extract().get('y_rep'))
print(y_rep_df_basic.shape)

(4000, 500)


In [12]:
def ppc_histogram(model_df, predictions_df, plot_slice,
                  model_data_color='SteelBlue',
                  predicted_data_color='LightBlue'):
    """Posterior Predictive Check histogram plot.

    Parameters
    ----------
    model_df : pandas.core.frame.DataFrame
        A pandas dataframe containing the model data.
    predictions_df : pandas.core.frame.DataFrame
        A pandas dataframe containing the predictions data.
    plot_slice : tuple, optional, default is (0, 8)
        A tuple indicating the slice in which to plot data
        from the predictions_df.
    model_data_color : string, optional, default is 'SteelBlue'
    predicted_data_color : string, optional, default is 'LightBlue'

    Returns
    -------
    grid : bokeh.models.layouts.Column
        A bokeh grid plot.
    """
    legend_plot = figure(plot_width=200, plot_height=200)
    a = legend_plot.vbar(
        x=[0],
        bottom=0,
        top=[1],
        width=[1],
        fill_color=model_data_color,
        line_color='Black',
        legend='Model data'
    )
    b = legend_plot.vbar(
        x=[0],
        bottom=0,
        top=[1],
        width=[1],
        fill_color=predicted_data_color,
        line_color='Black',
        legend='Predicted data'
    )
    legend_plot.axis.visible = False
    legend_plot.grid.visible = False
    legend_plot.outline_line_color = None
    a.visible = False
    b.visible = False

    plots = []
    n_plots = np.abs(np.diff(plot_slice))[0]
    titles = []
    title_sources = []
    sources = []
    for i in range(n_plots + 2):
        if i == 0:
            data = model_df['data'].values
            color = model_data_color
            counts, bins = np.histogram(data, bins='sturges')
            bin_width = bins[1] - bins[0]
            source = ColumnDataSource({'counts': counts, 'bins': bins[1:]})
            sources.append(source)
            titles.append('given data')
        else:
            for column in range(*plot_slice):
                data = predictions_df[column].values
                color = predicted_data_color
                counts, bins = np.histogram(data, bins='sturges')
                bin_width = bins[1] - bins[0]
                source = ColumnDataSource({'counts': counts, 'bins': bins[1:]})
                sources.append(source)
                titles.append(column)

        locals()['histogram_plot_{}'.format(i)] = figure(
            plot_width=200,
            plot_height=200,
            title='{}'.format(titles[i])
        )
        locals()['histogram_plot_{}'.format(i)].vbar(
            x='bins',
            bottom=0,
            top='counts',
            width=bin_width,
            fill_color=color,
            line_color='Black',
            source=source
        )
        plots.append(locals()['histogram_plot_{}'.format(i)])
    plots_grid = []
    temp_plots = []
    for i, plot in enumerate(plots[1:]):
        if len(temp_plots) == 3 and i != len(plots[1:]) - 1:
            temp_plots.append(plot)
            plots_grid.append(temp_plots)
            temp_plots = []
        elif i == len(plots[1:]) - 1:
            plots_grid.append(temp_plots)
        else:
            temp_plots.append(plot)
    plots_grid.insert(0, [plots[0], legend_plot])
    plots_grid = [plot for plot in plots_grid if plot]
    grid = gridplot(plots_grid, toolbar_location=None)

    return grid

In [13]:
grid = ppc_histogram(model_df, y_rep_df_basic, (0, 8))
show(grid)

## Compare density estimate of `y` to density estimates of a bunch of `y_refs`

In [14]:
# Style the figure.
density_title = 'Stan Con 2018 Introduction - Stan fit y_ref densities'

# Create the figure.
plot = figure(
    plot_width=plot_width,
    plot_height=plot_height,
    title=density_title
)

xs = []
ys = []
# Collect data for the figure.
for column in y_rep_df_basic.columns[:50]:
    data = y_rep_df_basic[column].values
    kde = sm.nonparametric.KDEUnivariate(data)
    kde.fit()
    xs.append(kde.support)
    ys.append(kde.density)

# Create the figure.
plot = figure(
    plot_width=plot_width,
    plot_height=plot_height,
    x_axis_label=x_axis_label,
    y_axis_label=y_axis_label,
    title=density_title
)

# Bind data to the figure.
plot.multi_line(
    xs=xs,
    ys=ys,
    line_width=1,
    line_alpha=0.4,
    hover_line_alpha=1.0,
    legend='y_rep'
)
_kde = sm.nonparametric.KDEUnivariate(model_df['data'].astype(float).values)
_kde.fit()
plot.line(_kde.support, _kde.density, color='Black', line_width=3, legend='y')

# # Show the figure.
show(plot)

## Compare proportion of zeros in y to the distribution of that proportion over all y_refs

In [15]:
model_df['data'].value_counts().get(0)/model_df['data'].shape[0]

0.202

In [16]:
zero_proportions = []
for column in y_rep_df_basic.columns:
    zero_proportions.append(y_rep_df_basic[column].value_counts().get(0)/y_rep_df_basic[column].shape[0])
counts, bins = np.histogram(zero_proportions, bins='auto')
bin_width = bins[1] - bins[0]
source = ColumnDataSource(
    {
        'counts': counts,
        'bins': bins[1:]
    }
)

plot = figure(
    plot_height=plot_height,
    plot_width=plot_width,
    x_axis_label='Zero count probabilities',
    y_axis_label='Frequencies',
    title='Stan Con 2018 Introduction - Zero probabilities',
    x_range=[0, 0.21]
)
plot.vbar(
    x='bins',
    width=bin_width,
    bottom=0,
    top='counts',
    source=source,
    fill_color='LightBlue',
#     line_color='Black',
)
vline = Span(
    location=model_df['data'].value_counts().get(0)/model_df['data'].shape[0],
    dimension='height',
#     line_color='Black',
    line_width=4
)
plot.renderers.extend([vline])

show(plot)

## Some other checks
Looking at two statistics in a scatterplot:

In [17]:
# Prepare the data for the plot.
means = []
stds = []
for column in y_rep_df_basic.columns:
    chains = np.array_split(y_rep_df_basic[column], 4)
    for chain in chains:
        means.append(chain.mean())
        stds.append(chain.std())
source = ColumnDataSource(
    {
        'std': stds,
        'mean': means
    }
)

# Create tools for the plot.
tools = 'pan,box_zoom,wheel_zoom,save,reset,help,crosshair'
hover = HoverTool(
    tooltips=[
        ('STD', '@std'),
        ('Mean', '@mean')
    ]
)
tools = tools.split(',') + [hover]

# Create the plot.
plot = figure(
    plot_width=plot_width,
    plot_height=plot_height,
    x_axis_label='Mean',
    y_axis_label='Standard Deviation',
    title='Stan Con 2018 Introduction - Scatterplot of y_rep STD vs Mean',
    tools=tools
)

# Bind data to the plot.
plot.circle(
    x='mean',
    y='std',
    source=source,
    size=10,
    fill_color='SteelBlue',
    line_color='White',
    legend='y_rep data'
)

model_source = ColumnDataSource({'mean': [model_df['data'].mean()], 'std': [model_df['data'].std()]})
plot.circle(
    x='mean',
    y='std',
    size=20,
    fill_color='Orange',
    line_color='Black',
    source=model_source,
    legend='model data'
)

show(plot)

## Fit Poisson "hurdle" model (also with truncation from above)

This model says that there is some probability `theta` that `y`
is zero and probability `1 - theta` that `y` is positive. 
Conditional on observing a positive `y`, we use a truncated 
Poisson

    y[n] ~ poisson(lambda) T[1, U];

where `T[1,U]` indicates truncation with lower bound `1` and upper bound `U`, 
which for simplicity we'll _assume_ is `max(y)`.

In [18]:
with open('../stan/poisson-hurdle.stan', 'r') as open_file:
    for line in open_file:
        print(line.replace('\n', ''))

/* Stan program 
 * for Poisson "hurdle" model (also with upper truncation)
 * 
 * Note: for simplicity I assume that there is only one way to obtain
 * a zero, as opposed to some zero-inflated models where there are 
 * multiple processes that lead to a zero. So in this example, y is 
 * zero with probability theta and y is modeled as a truncated poisson
 * if greater than zero.
 */

data {
  int<lower=1> N;
  int<lower=0> y[N];
}
transformed data {
  int U = max(y);  // upper truncation point
}
parameters {
  real<lower=0,upper=1> theta; // Pr(y = 0)
  real<lower=0> lambda; // Poisson rate parameter (if y > 0)
}
model {
  lambda ~ exponential(0.2);
  
  for (n in 1:N) {
    if (y[n] == 0) {
      target += log(theta);  // log(Pr(y = 0))
    } else {
      target += log1m(theta);  // log(Pr(y > 0))
      y[n] ~ poisson(lambda) T[1,U];  // truncated poisson
    }
  }
}
generated quantities {
  int y_rep[N];    // Draws from posterior preditive dist
  real log_lik[N]; // Pointwise log-l

In [19]:
hurdle_fit_data = {
    'N': model_df.shape[0],
    'y': model_df['data']
}
hurdle_fit = pystan.stan(
    file='../stan/poisson-hurdle.stan',
    data=hurdle_fit_data,
    iter=2000,
    warmup=1000,
    chains=4
)
print(hurdle_fit)

INFO:pystan:COMPILING THE C++ CODE FOR MODEL anon_model_aabe787a892626412154142c679f5c24 NOW.


Inference for Stan model: anon_model_aabe787a892626412154142c679f5c24.
4 chains, each with iter=2000; warmup=1000; thin=1; 
post-warmup draws per chain=1000, total post-warmup draws=4000.

               mean se_mean     sd   2.5%    25%    50%    75%  97.5%  n_eff   Rhat
theta           0.2  3.1e-4   0.02   0.17   0.19    0.2   0.22   0.24   3589    1.0
lambda          5.3  2.6e-3   0.16   4.99   5.19    5.3   5.41   5.63   3793    1.0
y_rep[0]       3.64    0.04   2.34    0.0    2.0    4.0    6.0    7.0   3903    1.0
y_rep[1]       3.67    0.04   2.35    0.0    2.0    4.0    6.0    7.0   4000    1.0
y_rep[2]       3.64    0.04   2.37    0.0    2.0    4.0    6.0    7.0   3937    1.0
y_rep[3]       3.63    0.04   2.38    0.0    2.0    4.0    6.0    7.0   4000    1.0
y_rep[4]       3.59    0.04   2.37    0.0    2.0    4.0    6.0    7.0   3779    1.0
y_rep[5]        3.6    0.04   2.34    0.0    2.0    4.0    5.0    7.0   4000    1.0
y_rep[6]       3.66    0.04   2.37    0.0    2.0    4.0

Before looking at the posterior distribution, think about whether you expect 
`lambda` to be larger or smaller than the `lambda` estimated using the simpler 
Poisson model. 

In [20]:
# Prepare the data for the plot. We will estimate the density of lambda to mimic
# what is available in R.
y = hurdle_fit.extract().get('lambda')
kde = sm.nonparametric.KDEUnivariate(y)
kde.fit(bw=0.012)
lambda_data = {
    'support': kde.support,
    'density': kde.density/kde.density.max()
}
lambda_source = ColumnDataSource(lambda_data)
eighty_percent = pd.DataFrame(
    kde.density/kde.density.max()
)[0].between(0.2, 0.8).replace(False, np.nan).dropna().index[[0, -1]].tolist()
band_x = np.append(
    kde.support[eighty_percent[0]:eighty_percent[1]],
    kde.support[eighty_percent[0]:eighty_percent[1]][::-1]
)
band_y = np.append(
    np.zeros(np.diff(eighty_percent)),
    kde.density[eighty_percent[0]:eighty_percent[-1]][::-1]/kde.density.max()
)

# Create tools specific to this plot.
tools = 'pan,box_zoom,wheel_zoom,save,reset,help'
lambda_hover = HoverTool(
    tooltips=[
        ('y', '@density'),
        ('x', '@support')
    ]
)
tools = tools.split(',') + [lambda_hover]

# Style the plot.
x_axis_label = 'lambda'
lambda_title = 'Stan Con 2018 Introduction - Stan fit lambda'

# Create the plot.
lambda_plot = figure(
    plot_width=plot_width,
    plot_height=plot_height,
    x_axis_label=x_axis_label,
    y_axis_label=y_axis_label,
    title=lambda_title,
    tools=tools
)

# Bind data to the plot.
lambda_plot.line(
    x='support',
    y='density',
    source=lambda_source,
    color='Black',
    line_width=2
)
vline = Span(location=y.mean(), dimension='height', line_color='DarkRed', line_width=2)
lambda_plot.renderers.extend([vline])
lambda_plot.patch(band_x, band_y, color='FireBrick', alpha=0.5)

# Show the plot.
show(lambda_plot)

In [21]:
y_rep_df_hurdle = pd.DataFrame(hurdle_fit.extract().get('y_rep'))
print(y_rep_df_hurdle.shape)

(4000, 500)


In [22]:
grid = ppc_histogram(model_df, y_rep_df_hurdle, (0, 8), model_data_color='FireBrick', predicted_data_color='Tomato')
show(grid)

In [23]:
# Style the figure.
density_title = 'Stan Con 2018 Introduction - Stan fit y_rep densities'

# Create the figure.
plot = figure(
    plot_width=plot_width,
    plot_height=plot_height,
    title=density_title
)

xs = []
ys = []
# Collect data for the figure.
for column in y_rep_df_hurdle.columns[:50]:
    data = y_rep_df_hurdle[column].values
    kde = sm.nonparametric.KDEUnivariate(data)
    kde.fit()
    xs.append(kde.support)
    ys.append(kde.density)

# Create the figure.
plot = figure(
    plot_width=plot_width,
    plot_height=plot_height,
    x_axis_label=x_axis_label,
    y_axis_label=y_axis_label,
    title=density_title
)

# Bind data to the figure.
plot.multi_line(
    xs=xs,
    ys=ys,
    line_width=1,
    line_alpha=0.1,
    hover_line_alpha=1.0,
    legend='y_rep',
    color='FireBrick'
)
_kde = sm.nonparametric.KDEUnivariate(model_df['data'].astype(float).values)
_kde.fit()
plot.line(_kde.support, _kde.density, color='Black', line_width=3, legend='y')

# # Show the figure.
show(plot)

In [24]:
zero_proportions = []
for column in y_rep_df_hurdle.columns:
    zero_proportions.append(y_rep_df_hurdle[column].value_counts().get(0)/y_rep_df_hurdle[column].shape[0])
counts, bins = np.histogram(zero_proportions, bins='auto')
bin_width = bins[1] - bins[0]
source = ColumnDataSource(
    {
        'counts': counts,
        'bins': bins[1:]
    }
)

plot = figure(
    plot_height=plot_height,
    plot_width=plot_width,
    x_axis_label='Zero count probabilities',
    y_axis_label='Frequencies',
    title='Stan Con 2018 Introduction - Zero probabilities',
#     x_range=[0, 0.21]
)
plot.vbar(
    x='bins',
    width=bin_width,
    bottom=0,
    top='counts',
    source=source,
    fill_color='FireBrick',
    line_color='Black',
    alpha=0.9
)
vline = Span(
    location=model_df['data'].value_counts().get(0)/model_df['data'].shape[0],
    dimension='height',
#     line_color='Black',
    line_width=4
)
plot.renderers.extend([vline])

show(plot)

In [25]:
# Prepare the data for the plot.
means = []
stds = []
for column in y_rep_df_hurdle.columns:
    chains = np.array_split(y_rep_df_hurdle[column], 4)
    for chain in chains:
        means.append(chain.mean())
        stds.append(chain.std())
source = ColumnDataSource(
    {
        'std': stds,
        'mean': means
    }
)

# Create tools for the plot.
tools = 'pan,box_zoom,wheel_zoom,save,reset,help,crosshair'
hover = HoverTool(
    tooltips=[
        ('STD', '@std'),
        ('Mean', '@mean')
    ]
)
tools = tools.split(',') + [hover]

# Create the plot.
plot = figure(
    plot_width=plot_width,
    plot_height=plot_height,
    x_axis_label='Mean',
    y_axis_label='Standard Deviation',
    title='Stan Con 2018 Introduction - Scatterplot of y_rep STD vs Mean',
    tools=tools
)

# Bind data to the plot.
plot.circle(
    x='mean',
    y='std',
    source=source,
    size=10,
    fill_color='FireBrick',
    line_color='White',
    legend='y_rep data',
    alpha=0.7
)

model_source = ColumnDataSource({'mean': [model_df['data'].mean()], 'std': [model_df['data'].std()]})
plot.circle(
    x='mean',
    y='std',
    size=20,
    fill_color='Orange',
    line_color='Black',
    source=model_source,
    legend='model data'
)

show(plot)

## How about the predictive performance with LOO?
Model 2 is a clear winner in the predictive performance.

In [26]:
basic_log_likelihood = basic_fit.extract().get('log_lik')
hurdle_log_likelihood = hurdle_fit.extract().get('log_lik')
log_likelihoods = [basic_log_likelihood, hurdle_log_likelihood]
basic_log_likelihood.shape

(4000, 500)

**`NOTE`** that running the R magic below will not output standard messages as shown in the `R` notebook with this analysis.

In [27]:
%%R -i log_likelihoods
library("loo")

basic_log_likelihood <- log_likelihoods[1]
basic_log_likelihood <- as.numeric(basic_log_likelihood[[1]])
basic_log_likelihood <- matrix(basic_log_likelihood, ncol = 500)

hurdle_log_likelihood <- log_likelihoods[2]
hurdle_log_likelihood <- as.numeric(hurdle_log_likelihood[[1]])
hurdle_log_likelihood <- matrix(hurdle_log_likelihood, ncol = 500)

loo_basic = loo(basic_log_likelihood)
loo_hurdle = loo(hurdle_log_likelihood)
compare(loo_basic, loo_hurdle)
# print(comparison)

/usr/local/miniconda3/envs/StanCon2018_Intro/lib/python3.6/site-packages/rpy2/rinterface/__init__.py:145: RRuntimeWarning: This is loo version 1.1.0

  warnings.warn(x, RRuntimeWarning)


elpd_diff        se 
    216.0      22.1 


---

---

---

---

---

---

---

---

---

---